In [5]:
from bs4 import BeautifulSoup
import pandas as pd
from datetime import datetime
import warnings
import time
import sklearn.preprocessing
import requests


pd.set_option("display.max_columns", None)
warnings.filterwarnings(action='ignore')

serviceKey='bwUUK6MEA6GnqDpo2ZS9ChN4VZ1nkUPXrryU80XxUcLqxB62pIGIPWXNdyzqgT20BHrw8zxWWk9rqiSQwTrbnQ=='

p7000 ={'serviceKey' :serviceKey,
             'routeId':'200000112','stationId':'228000703'}
class Bus():
    def __init__(self,params):
        self.params=params
        self.bus_time=[]
        
    def repet(self):
        url = 'http://apis.data.go.kr/6410000/busarrivalservice/getBusArrivalItem'
        response = requests.get(url, params=self.params)
        soup=BeautifulSoup(response.text,'xml')
        return soup

        
    def current_buses(self): 
        url = 'http://apis.data.go.kr/6410000/buslocationservice/getBusLocationList'
        mod_params ={'serviceKey' : self.params['serviceKey'],
                  'routeId':self.params['routeId']}

        response=requests.get(url,params=mod_params)
        soup=BeautifulSoup(response.text,'xml')
        locations=sorted([int(x.stationSeq.text) for x in soup.find_all('busLocationList')])
        return locations


def trim_data(df,FileName):
    df['시간'] = df['시간'].apply(pd.to_datetime)
    df['hour']=df['시간'].dt.hour
    df['minute']=df['시간'].dt.minute
    df['second']=df['시간'].dt.second
    df['day'] = df['시간'].dt.weekday 

    mb = sklearn.preprocessing.MultiLabelBinarizer()
    if isinstance(df['운행중인 다른 버스들의 위치'].iloc[0], str):
        df['운행중인 다른 버스들의 위치'] = df['운행중인 다른 버스들의 위치'].apply(eval)
    entity = mb.fit_transform(df['운행중인 다른 버스들의 위치']) 
    lsts=pd.DataFrame(entity,columns=mb.classes_)
    lsts.columns=[f'station{x}' for x in lsts.columns]
    df=pd.concat([df,lsts],axis=1,sort=False).reset_index(drop=True)


    df=df.drop(["운행중인 다른 버스들의 위치"],axis=1)
    
    batch=df.index[df.arrived==1]
    df=df.iloc[:batch[-1]+1,:]
    #7/12 -----------------------------------
    batch=df.index[df.arrived==1]
    temp=0
    for x in batch:
        for y in range(temp,x): 
            df['arrived'][y]=(df['시간'][x]-df['시간'][y]).seconds
            temp=x+1
    for e in batch:
        df['arrived'][e]=0
    # 7/12 -----------------------------------

    df = df.set_index('시간')
    df.to_csv(f'./{FileName}')        # 동일 폴더에 파일이 저장될 거임
    return df





In [6]:

past=4
pBus=Bus(p7000)
for x in range(720): # 시간 설정
    soup=pBus.repet()
    try:
        result=int(soup.resultCode.text)
        arrived=0
        if past!=result:
            if result==0:
                arrived=1
        pBus.bus_time.append([soup.queryTime.text,pBus.current_buses(),arrived])
        past=result
        print(x,"번째 시도: ",pBus.bus_time)
        time.sleep(60)
    except Exception as e:
        continue

df=pd.DataFrame(pBus.bus_time,columns=['시간','운행중인 다른 버스들의 위치','arrived'])

mod_df=trim_data(df,'7000_8.8.csv') # 이름 설정
mod_df

0 번째 시도:  [['2022-08-08 11:13:15.802', [10, 19, 27, 33, 45, 51, 62, 73], 0]]
1 번째 시도:  [['2022-08-08 11:13:15.802', [10, 19, 27, 33, 45, 51, 62, 73], 0], ['2022-08-08 11:14:15.988', [10, 19, 27, 34, 46, 51, 63, 74], 0]]
2 번째 시도:  [['2022-08-08 11:13:15.802', [10, 19, 27, 33, 45, 51, 62, 73], 0], ['2022-08-08 11:14:15.988', [10, 19, 27, 34, 46, 51, 63, 74], 0], ['2022-08-08 11:15:31.175', [11, 21, 28, 35, 47, 51, 64, 76], 0]]
3 번째 시도:  [['2022-08-08 11:13:15.802', [10, 19, 27, 33, 45, 51, 62, 73], 0], ['2022-08-08 11:14:15.988', [10, 19, 27, 34, 46, 51, 63, 74], 0], ['2022-08-08 11:15:31.175', [11, 21, 28, 35, 47, 51, 64, 76], 0], ['2022-08-08 11:16:31.315', [1, 11, 22, 28, 36, 48, 51, 65, 77], 1]]
4 번째 시도:  [['2022-08-08 11:13:15.802', [10, 19, 27, 33, 45, 51, 62, 73], 0], ['2022-08-08 11:14:15.988', [10, 19, 27, 34, 46, 51, 63, 74], 0], ['2022-08-08 11:15:31.175', [11, 21, 28, 35, 47, 51, 64, 76], 0], ['2022-08-08 11:16:31.315', [1, 11, 22, 28, 36, 48, 51, 65, 77], 1], ['2022-08-08 11

16 번째 시도:  [['2022-08-08 11:13:15.802', [10, 19, 27, 33, 45, 51, 62, 73], 0], ['2022-08-08 11:14:15.988', [10, 19, 27, 34, 46, 51, 63, 74], 0], ['2022-08-08 11:15:31.175', [11, 21, 28, 35, 47, 51, 64, 76], 0], ['2022-08-08 11:16:31.315', [1, 11, 22, 28, 36, 48, 51, 65, 77], 1], ['2022-08-08 11:17:31.470', [3, 11, 23, 29, 37, 48, 52, 65, 79], 0], ['2022-08-08 11:18:31.657', [3, 13, 24, 29, 38, 48, 52, 66, 79], 0], ['2022-08-08 11:19:31.797', [3, 13, 24, 29, 38, 49, 52, 68], 0], ['2022-08-08 11:20:31.953', [4, 14, 24, 31, 38, 50, 53, 68], 0], ['2022-08-08 11:21:32.124', [5, 15, 25, 31, 39, 50, 53, 69], 0], ['2022-08-08 11:22:32.288', [6, 16, 26, 32, 40, 51, 53, 69], 0], ['2022-08-08 11:23:32.436', [7, 16, 26, 32, 40, 51, 54, 69], 0], ['2022-08-08 11:24:32.607', [7, 17, 26, 33, 40, 51, 54, 70], 0], ['2022-08-08 11:25:32.810', [7, 18, 26, 34, 41, 52, 55, 71], 0], ['2022-08-08 11:26:34.309', [8, 19, 26, 34, 41, 52, 55, 71], 0], ['2022-08-08 11:27:34.481', [9, 19, 27, 36, 42, 52, 56, 73], 0]

23 번째 시도:  [['2022-08-08 11:13:15.802', [10, 19, 27, 33, 45, 51, 62, 73], 0], ['2022-08-08 11:14:15.988', [10, 19, 27, 34, 46, 51, 63, 74], 0], ['2022-08-08 11:15:31.175', [11, 21, 28, 35, 47, 51, 64, 76], 0], ['2022-08-08 11:16:31.315', [1, 11, 22, 28, 36, 48, 51, 65, 77], 1], ['2022-08-08 11:17:31.470', [3, 11, 23, 29, 37, 48, 52, 65, 79], 0], ['2022-08-08 11:18:31.657', [3, 13, 24, 29, 38, 48, 52, 66, 79], 0], ['2022-08-08 11:19:31.797', [3, 13, 24, 29, 38, 49, 52, 68], 0], ['2022-08-08 11:20:31.953', [4, 14, 24, 31, 38, 50, 53, 68], 0], ['2022-08-08 11:21:32.124', [5, 15, 25, 31, 39, 50, 53, 69], 0], ['2022-08-08 11:22:32.288', [6, 16, 26, 32, 40, 51, 53, 69], 0], ['2022-08-08 11:23:32.436', [7, 16, 26, 32, 40, 51, 54, 69], 0], ['2022-08-08 11:24:32.607', [7, 17, 26, 33, 40, 51, 54, 70], 0], ['2022-08-08 11:25:32.810', [7, 18, 26, 34, 41, 52, 55, 71], 0], ['2022-08-08 11:26:34.309', [8, 19, 26, 34, 41, 52, 55, 71], 0], ['2022-08-08 11:27:34.481', [9, 19, 27, 36, 42, 52, 56, 73], 0]

28 번째 시도:  [['2022-08-08 11:13:15.802', [10, 19, 27, 33, 45, 51, 62, 73], 0], ['2022-08-08 11:14:15.988', [10, 19, 27, 34, 46, 51, 63, 74], 0], ['2022-08-08 11:15:31.175', [11, 21, 28, 35, 47, 51, 64, 76], 0], ['2022-08-08 11:16:31.315', [1, 11, 22, 28, 36, 48, 51, 65, 77], 1], ['2022-08-08 11:17:31.470', [3, 11, 23, 29, 37, 48, 52, 65, 79], 0], ['2022-08-08 11:18:31.657', [3, 13, 24, 29, 38, 48, 52, 66, 79], 0], ['2022-08-08 11:19:31.797', [3, 13, 24, 29, 38, 49, 52, 68], 0], ['2022-08-08 11:20:31.953', [4, 14, 24, 31, 38, 50, 53, 68], 0], ['2022-08-08 11:21:32.124', [5, 15, 25, 31, 39, 50, 53, 69], 0], ['2022-08-08 11:22:32.288', [6, 16, 26, 32, 40, 51, 53, 69], 0], ['2022-08-08 11:23:32.436', [7, 16, 26, 32, 40, 51, 54, 69], 0], ['2022-08-08 11:24:32.607', [7, 17, 26, 33, 40, 51, 54, 70], 0], ['2022-08-08 11:25:32.810', [7, 18, 26, 34, 41, 52, 55, 71], 0], ['2022-08-08 11:26:34.309', [8, 19, 26, 34, 41, 52, 55, 71], 0], ['2022-08-08 11:27:34.481', [9, 19, 27, 36, 42, 52, 56, 73], 0]

33 번째 시도:  [['2022-08-08 11:13:15.802', [10, 19, 27, 33, 45, 51, 62, 73], 0], ['2022-08-08 11:14:15.988', [10, 19, 27, 34, 46, 51, 63, 74], 0], ['2022-08-08 11:15:31.175', [11, 21, 28, 35, 47, 51, 64, 76], 0], ['2022-08-08 11:16:31.315', [1, 11, 22, 28, 36, 48, 51, 65, 77], 1], ['2022-08-08 11:17:31.470', [3, 11, 23, 29, 37, 48, 52, 65, 79], 0], ['2022-08-08 11:18:31.657', [3, 13, 24, 29, 38, 48, 52, 66, 79], 0], ['2022-08-08 11:19:31.797', [3, 13, 24, 29, 38, 49, 52, 68], 0], ['2022-08-08 11:20:31.953', [4, 14, 24, 31, 38, 50, 53, 68], 0], ['2022-08-08 11:21:32.124', [5, 15, 25, 31, 39, 50, 53, 69], 0], ['2022-08-08 11:22:32.288', [6, 16, 26, 32, 40, 51, 53, 69], 0], ['2022-08-08 11:23:32.436', [7, 16, 26, 32, 40, 51, 54, 69], 0], ['2022-08-08 11:24:32.607', [7, 17, 26, 33, 40, 51, 54, 70], 0], ['2022-08-08 11:25:32.810', [7, 18, 26, 34, 41, 52, 55, 71], 0], ['2022-08-08 11:26:34.309', [8, 19, 26, 34, 41, 52, 55, 71], 0], ['2022-08-08 11:27:34.481', [9, 19, 27, 36, 42, 52, 56, 73], 0]

...

401 번째 시도:  [['2022-08-08 11:13:15.802', [10, 19, 27, 33, 45, 51, 62, 73], 0], ['2022-08-08 11:14:15.988', [10, 19, 27, 34, 46, 51, 63, 74], 0], ['2022-08-08 11:15:31.175', [11, 21, 28, 35, 47, 51, 64, 76], 0], ['2022-08-08 11:16:31.315', [1, 11, 22, 28, 36, 48, 51, 65, 77], 1], ['2022-08-08 11:17:31.470', [3, 11, 23, 29, 37, 48, 52, 65, 79], 0], ['2022-08-08 11:18:31.657', [3, 13, 24, 29, 38, 48, 52, 66, 79], 0], ['2022-08-08 11:19:31.797', [3, 13, 24, 29, 38, 49, 52, 68], 0], ['2022-08-08 11:20:31.953', [4, 14, 24, 31, 38, 50, 53, 68], 0], ['2022-08-08 11:21:32.124', [5, 15, 25, 31, 39, 50, 53, 69], 0], ['2022-08-08 11:22:32.288', [6, 16, 26, 32, 40, 51, 53, 69], 0], ['2022-08-08 11:23:32.436', [7, 16, 26, 32, 40, 51, 54, 69], 0], ['2022-08-08 11:24:32.607', [7, 17, 26, 33, 40, 51, 54, 70], 0], ['2022-08-08 11:25:32.810', [7, 18, 26, 34, 41, 52, 55, 71], 0], ['2022-08-08 11:26:34.309', [8, 19, 26, 34, 41, 52, 55, 71], 0], ['2022-08-08 11:27:34.481', [9, 19, 27, 36, 42, 52, 56, 73], 0

402 번째 시도:  [['2022-08-08 11:13:15.802', [10, 19, 27, 33, 45, 51, 62, 73], 0], ['2022-08-08 11:14:15.988', [10, 19, 27, 34, 46, 51, 63, 74], 0], ['2022-08-08 11:15:31.175', [11, 21, 28, 35, 47, 51, 64, 76], 0], ['2022-08-08 11:16:31.315', [1, 11, 22, 28, 36, 48, 51, 65, 77], 1], ['2022-08-08 11:17:31.470', [3, 11, 23, 29, 37, 48, 52, 65, 79], 0], ['2022-08-08 11:18:31.657', [3, 13, 24, 29, 38, 48, 52, 66, 79], 0], ['2022-08-08 11:19:31.797', [3, 13, 24, 29, 38, 49, 52, 68], 0], ['2022-08-08 11:20:31.953', [4, 14, 24, 31, 38, 50, 53, 68], 0], ['2022-08-08 11:21:32.124', [5, 15, 25, 31, 39, 50, 53, 69], 0], ['2022-08-08 11:22:32.288', [6, 16, 26, 32, 40, 51, 53, 69], 0], ['2022-08-08 11:23:32.436', [7, 16, 26, 32, 40, 51, 54, 69], 0], ['2022-08-08 11:24:32.607', [7, 17, 26, 33, 40, 51, 54, 70], 0], ['2022-08-08 11:25:32.810', [7, 18, 26, 34, 41, 52, 55, 71], 0], ['2022-08-08 11:26:34.309', [8, 19, 26, 34, 41, 52, 55, 71], 0], ['2022-08-08 11:27:34.481', [9, 19, 27, 36, 42, 52, 56, 73], 0

403 번째 시도:  [['2022-08-08 11:13:15.802', [10, 19, 27, 33, 45, 51, 62, 73], 0], ['2022-08-08 11:14:15.988', [10, 19, 27, 34, 46, 51, 63, 74], 0], ['2022-08-08 11:15:31.175', [11, 21, 28, 35, 47, 51, 64, 76], 0], ['2022-08-08 11:16:31.315', [1, 11, 22, 28, 36, 48, 51, 65, 77], 1], ['2022-08-08 11:17:31.470', [3, 11, 23, 29, 37, 48, 52, 65, 79], 0], ['2022-08-08 11:18:31.657', [3, 13, 24, 29, 38, 48, 52, 66, 79], 0], ['2022-08-08 11:19:31.797', [3, 13, 24, 29, 38, 49, 52, 68], 0], ['2022-08-08 11:20:31.953', [4, 14, 24, 31, 38, 50, 53, 68], 0], ['2022-08-08 11:21:32.124', [5, 15, 25, 31, 39, 50, 53, 69], 0], ['2022-08-08 11:22:32.288', [6, 16, 26, 32, 40, 51, 53, 69], 0], ['2022-08-08 11:23:32.436', [7, 16, 26, 32, 40, 51, 54, 69], 0], ['2022-08-08 11:24:32.607', [7, 17, 26, 33, 40, 51, 54, 70], 0], ['2022-08-08 11:25:32.810', [7, 18, 26, 34, 41, 52, 55, 71], 0], ['2022-08-08 11:26:34.309', [8, 19, 26, 34, 41, 52, 55, 71], 0], ['2022-08-08 11:27:34.481', [9, 19, 27, 36, 42, 52, 56, 73], 0

404 번째 시도:  [['2022-08-08 11:13:15.802', [10, 19, 27, 33, 45, 51, 62, 73], 0], ['2022-08-08 11:14:15.988', [10, 19, 27, 34, 46, 51, 63, 74], 0], ['2022-08-08 11:15:31.175', [11, 21, 28, 35, 47, 51, 64, 76], 0], ['2022-08-08 11:16:31.315', [1, 11, 22, 28, 36, 48, 51, 65, 77], 1], ['2022-08-08 11:17:31.470', [3, 11, 23, 29, 37, 48, 52, 65, 79], 0], ['2022-08-08 11:18:31.657', [3, 13, 24, 29, 38, 48, 52, 66, 79], 0], ['2022-08-08 11:19:31.797', [3, 13, 24, 29, 38, 49, 52, 68], 0], ['2022-08-08 11:20:31.953', [4, 14, 24, 31, 38, 50, 53, 68], 0], ['2022-08-08 11:21:32.124', [5, 15, 25, 31, 39, 50, 53, 69], 0], ['2022-08-08 11:22:32.288', [6, 16, 26, 32, 40, 51, 53, 69], 0], ['2022-08-08 11:23:32.436', [7, 16, 26, 32, 40, 51, 54, 69], 0], ['2022-08-08 11:24:32.607', [7, 17, 26, 33, 40, 51, 54, 70], 0], ['2022-08-08 11:25:32.810', [7, 18, 26, 34, 41, 52, 55, 71], 0], ['2022-08-08 11:26:34.309', [8, 19, 26, 34, 41, 52, 55, 71], 0], ['2022-08-08 11:27:34.481', [9, 19, 27, 36, 42, 52, 56, 73], 0

ConnectionError: HTTPConnectionPool(host='apis.data.go.kr', port=80): Max retries exceeded with url: /6410000/busarrivalservice/getBusArrivalItem?serviceKey=bwUUK6MEA6GnqDpo2ZS9ChN4VZ1nkUPXrryU80XxUcLqxB62pIGIPWXNdyzqgT20BHrw8zxWWk9rqiSQwTrbnQ%3D%3D&routeId=200000112&stationId=228000703 (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x0000013C0C4F1070>: Failed to establish a new connection: [WinError 10060] 연결된 구성원으로부터 응답이 없어 연결하지 못했거나, 호스트로부터 응답이 없어 연결이 끊어졌습니다'))